# Lux AI Deep Reinforcement Learning Environment Example
See https://github.com/glmcdona/LuxPythonEnvGym for environment project and updates.

This is a python replica of the Lux game engine to speed up training. It reformats the agent problem into making a action decision per-unit for the team.

In [1]:
!pip install git+https://github.com/glmcdona/LuxPythonEnvGym.git
!pip install kaggle-environments -U

  Cloning https://github.com/glmcdona/LuxPythonEnvGym.git to /private/var/folders/4z/7rrlsr756fjg6jq7c4jy9fzc0000gn/T/pip-req-build-1rh61a64
  Running command git clone -q https://github.com/glmcdona/LuxPythonEnvGym.git /private/var/folders/4z/7rrlsr756fjg6jq7c4jy9fzc0000gn/T/pip-req-build-1rh61a64
  Resolved https://github.com/glmcdona/LuxPythonEnvGym.git to commit 55e8ddc15012fd55f17b23aa2e73c919467e43e3
  Using cached stable_baselines3-1.2.1a2-py3-none-any.whl (173 kB)
  Using cached tensorboard-2.7.0-py3-none-any.whl (5.8 MB)
  Using cached gym-0.19.0-py3-none-any.whl
  Using cached cloudpickle-1.6.0-py3-none-any.whl (23 kB)
  Using cached torch-1.10.0-cp37-none-macosx_10_9_x86_64.whl (147.1 MB)
     |████████████████████████████████| 1.0 MB 3.9 MB/s eta 0:00:01
  Using cached Markdown-3.3.6-py3-none-any.whl (97 kB)
  Using cached google_auth-2.3.3-py2.py3-none-any.whl (155 kB)
  Using cached tensorboard_plugin_wit-1.8.0-py3-none-any.whl (781 kB)
  Using cached google_auth_oauthlib

  Using cached kaggle_environments-1.8.12-py2.py3-none-any.whl (1.2 MB)


## Use GPU if available
Note: GPU provides very little speedup. I recommend using a CPU-only notebook usually.

In [1]:
import torch
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device
print(device)

cpu


# Define the RL agent logic
Edit this agent logic to implement your own observations, action space, and reward shaping.

In [19]:
%%writefile agent_policy.py
from luxai2021.game.match_controller import ActionSequence
import sys
import time
from functools import partial  # pip install functools

import numpy as np
from gym import spaces
import copy
import random

from luxai2021.env.agent import Agent
from luxai2021.game.actions import *
from luxai2021.game.game_constants import GAME_CONSTANTS
from luxai2021.game.position import Position


# https://codereview.stackexchange.com/questions/28207/finding-the-closest-point-to-a-list-of-points
def closest_node(node, nodes):
    dist_2 = np.sum((nodes - node) ** 2, axis=1)
    return np.argmin(dist_2)
def furthest_node(node, nodes):
    dist_2 = np.sum((nodes - node) ** 2, axis=1)
    return np.argmax(dist_2)

def smart_transfer_to_nearby(game, team, unit_id, unit, target_type_restriction=None, **kwarg):
    """
    Smart-transfers from the specified unit to a nearby neighbor. Prioritizes any
    nearby carts first, then any worker. Transfers the resource type which the unit
    has most of. Picks which cart/worker based on choosing a target that is most-full
    but able to take the most amount of resources.

    Args:
        team ([type]): [description]
        unit_id ([type]): [description]

    Returns:
        Action: Returns a TransferAction object, even if the request is an invalid
                transfer. Use TransferAction.is_valid() to check validity.
    """

    # Calculate how much resources could at-most be transferred
    resource_type = None
    resource_amount = 0
    target_unit = None

    if unit != None:
        for type, amount in unit.cargo.items():
            if amount > resource_amount:
                resource_type = type
                resource_amount = amount

        # Find the best nearby unit to transfer to
        unit_cell = game.map.get_cell_by_pos(unit.pos)
        adjacent_cells = game.map.get_adjacent_cells(unit_cell)

        
        for c in adjacent_cells:
            for id, u in c.units.items():
                # Apply the unit type target restriction
                if target_type_restriction == None or u.type == target_type_restriction:
                    if u.team == team:
                        # This unit belongs to our team, set it as the winning transfer target
                        # if it's the best match.
                        if target_unit is None:
                            target_unit = u
                        else:
                            # Compare this unit to the existing target
                            if target_unit.type == u.type:
                                # Transfer to the target with the least capacity, but can accept
                                # all of our resources
                                if( u.get_cargo_space_left() >= resource_amount and 
                                    target_unit.get_cargo_space_left() >= resource_amount ):
                                    # Both units can accept all our resources. Prioritize one that is most-full.
                                    if u.get_cargo_space_left() < target_unit.get_cargo_space_left():
                                        # This new target it better, it has less space left and can take all our
                                        # resources
                                        target_unit = u
                                    
                                elif( target_unit.get_cargo_space_left() >= resource_amount ):
                                    # Don't change targets. Current one is best since it can take all
                                    # the resources, but new target can't.
                                    pass
                                    
                                elif( u.get_cargo_space_left() > target_unit.get_cargo_space_left() ):
                                    # Change targets, because neither target can accept all our resources and 
                                    # this target can take more resources.
                                    target_unit = u
                            elif u.type == Constants.UNIT_TYPES.CART:
                                # Transfer to this cart instead of the current worker target
                                target_unit = u
    
    # Build the transfer action request
    target_unit_id = None
    if target_unit is not None:
        target_unit_id = target_unit.id

        # Update the transfer amount based on the room of the target
        if target_unit.get_cargo_space_left() < resource_amount:
            resource_amount = target_unit.get_cargo_space_left()
    
    return TransferAction(team, unit_id, target_unit_id, resource_type, resource_amount)

########################################################################################################################
# This is the Agent that you need to design for the competition
########################################################################################################################
class AgentPolicy(Agent):
    def __init__(self, mode="train", model=None) -> None:
        """
        Arguments:
            mode: "train" or "inference", which controls if this agent is for training or not.
            model: The pretrained model, or if None it will operate in training mode.
        """
        super().__init__()
        self.model = model
        self.mode = mode
        self.step_count = 0
        self.stats = None
        self.stats_last_game = None

        # Define action and observation space
        # They must be gym.spaces objects
        # Example when using discrete actions:
        self.actionSpaceMapUnits = [
            partial(MoveAction, direction=Constants.DIRECTIONS.CENTER),  # This is the do-nothing action
            partial(MoveAction, direction=Constants.DIRECTIONS.NORTH),
            partial(MoveAction, direction=Constants.DIRECTIONS.WEST),
            partial(MoveAction, direction=Constants.DIRECTIONS.SOUTH),
            partial(MoveAction, direction=Constants.DIRECTIONS.EAST),
            smart_transfer_to_nearby, # Transfer to nearby
            SpawnCityAction,
            #PillageAction,
        ]
        self.actionSpaceMapCities = [
            SpawnWorkerAction,
            SpawnCartAction,
            ResearchAction,
        ]

        self.action_space = spaces.Discrete(max(len(self.actionSpaceMapUnits), len(self.actionSpaceMapCities)))
        

        # Observation space: (Basic minimum for a miner agent)
        # Object:
        #   1x is worker
        #   1x is cart
        #   1x is citytile
        #
        #   5x direction_nearest_wood
        #   1x distance_nearest_wood
        #   1x amount
        #
        #   5x direction_nearest_coal
        #   1x distance_nearest_coal
        #   1x amount
        #
        #   5x direction_nearest_uranium
        #   1x distance_nearest_uranium
        #   1x amount
        #
        #   5x direction_nearest_city
        #   1x distance_nearest_city
        #   1x amount of fuel
        #
        #   28x (the same as above, but direction, distance, and amount to the furthest of each)
        #
        #   5x direction_nearest_worker
        #   1x distance_nearest_worker
        #   1x amount of cargo
        # Unit:
        #   1x cargo size
        # State:
        #   1x is night
        #   1x percent of game done
        #   2x citytile counts [cur player, opponent]
        #   2x worker counts [cur player, opponent]
        #   2x cart counts [cur player, opponent]
        #   1x research points [cur player]
        #   1x researched coal [cur player]
        #   1x researched uranium [cur player]
        self.observation_shape = (3 + 7 * 5 * 2 + 1 + 1 + 1 + 2 + 2 + 2 + 3,)
        self.observation_space = spaces.Box(low=0, high=1, shape=
        self.observation_shape, dtype=np.float16)

        self.object_nodes = {}

    def get_agent_type(self):
        """
        Returns the type of agent. Use AGENT for inference, and LEARNING for training a model.
        """
        if self.mode == "train":
            return Constants.AGENT_TYPE.LEARNING
        else:
            return Constants.AGENT_TYPE.AGENT

    def get_observation(self, game, unit, city_tile, team, is_new_turn):
        """
        Implements getting a observation from the current game for this unit or city
        """
        observation_index = 0
        if is_new_turn:
            # It's a new turn this event. This flag is set True for only the first observation from each turn.
            # Update any per-turn fixed observation space that doesn't change per unit/city controlled.

            # Build a list of object nodes by type for quick distance-searches
            self.object_nodes = {}

            # Add resources
            for cell in game.map.resources:
                if cell.resource.type not in self.object_nodes:
                    self.object_nodes[cell.resource.type] = np.array([[cell.pos.x, cell.pos.y]])
                else:
                    self.object_nodes[cell.resource.type] = np.concatenate(
                        (
                            self.object_nodes[cell.resource.type],
                            [[cell.pos.x, cell.pos.y]]
                        ),
                        axis=0
                    )

            # Add your own and opponent units
            for t in [team, (team + 1) % 2]:
                for u in game.state["teamStates"][team]["units"].values():
                    key = str(u.type)
                    if t != team:
                        key = str(u.type) + "_opponent"

                    if key not in self.object_nodes:
                        self.object_nodes[key] = np.array([[u.pos.x, u.pos.y]])
                    else:
                        self.object_nodes[key] = np.concatenate(
                            (
                                self.object_nodes[key],
                                [[u.pos.x, u.pos.y]]
                            )
                            , axis=0
                        )

            # Add your own and opponent cities
            for city in game.cities.values():
                for cells in city.city_cells:
                    key = "city"
                    if city.team != team:
                        key = "city_opponent"

                    if key not in self.object_nodes:
                        self.object_nodes[key] = np.array([[cells.pos.x, cells.pos.y]])
                    else:
                        self.object_nodes[key] = np.concatenate(
                            (
                                self.object_nodes[key],
                                [[cells.pos.x, cells.pos.y]]
                            )
                            , axis=0
                        )

        # Observation space: (Basic minimum for a miner agent)
        # Object:
        #   1x is worker
        #   1x is cart
        #   1x is citytile
        #   5x direction_nearest_wood
        #   1x distance_nearest_wood
        #   1x amount
        #
        #   5x direction_nearest_coal
        #   1x distance_nearest_coal
        #   1x amount
        #
        #   5x direction_nearest_uranium
        #   1x distance_nearest_uranium
        #   1x amount
        #
        #   5x direction_nearest_city
        #   1x distance_nearest_city
        #   1x amount of fuel
        #
        #   5x direction_nearest_worker
        #   1x distance_nearest_worker
        #   1x amount of cargo
        #
        #   28x (the same as above, but direction, distance, and amount to the furthest of each)
        #
        # Unit:
        #   1x cargo size
        # State:
        #   1x is night
        #   1x percent of game done
        #   2x citytile counts [cur player, opponent]
        #   2x worker counts [cur player, opponent]
        #   2x cart counts [cur player, opponent]
        #   1x research points [cur player]
        #   1x researched coal [cur player]
        #   1x researched uranium [cur player]
        obs = np.zeros(self.observation_shape)
        
        # Update the type of this object
        #   1x is worker
        #   1x is cart
        #   1x is citytile
        observation_index = 0
        if unit is not None:
            if unit.type == Constants.UNIT_TYPES.WORKER:
                obs[observation_index] = 1.0 # Worker
            else:
                obs[observation_index+1] = 1.0 # Cart
        if city_tile is not None:
            obs[observation_index+2] = 1.0 # CityTile
        observation_index += 3
        
        pos = None
        if unit is not None:
            pos = unit.pos
        else:
            pos = city_tile.pos

        if pos is None:
            observation_index += 7 * 5 * 2
        else:
            # Encode the direction to the nearest objects
            #   5x direction_nearest
            #   1x distance
            for distance_function in [closest_node, furthest_node]:
                for key in [
                    Constants.RESOURCE_TYPES.WOOD,
                    Constants.RESOURCE_TYPES.COAL,
                    Constants.RESOURCE_TYPES.URANIUM,
                    "city",
                    str(Constants.UNIT_TYPES.WORKER)]:
                    # Process the direction to and distance to this object type

                    # Encode the direction to the nearest object (excluding itself)
                    #   5x direction
                    #   1x distance
                    if key in self.object_nodes:
                        if (
                                (key == "city" and city_tile is not None) or
                                (unit is not None and str(unit.type) == key and len(game.map.get_cell_by_pos(unit.pos).units) <= 1 )
                        ):
                            # Filter out the current unit from the closest-search
                            closest_index = closest_node((pos.x, pos.y), self.object_nodes[key])
                            filtered_nodes = np.delete(self.object_nodes[key], closest_index, axis=0)
                        else:
                            filtered_nodes = self.object_nodes[key]

                        if len(filtered_nodes) == 0:
                            # No other object of this type
                            obs[observation_index + 5] = 1.0
                        else:
                            # There is another object of this type
                            closest_index = distance_function((pos.x, pos.y), filtered_nodes)

                            if closest_index is not None and closest_index >= 0:
                                closest = filtered_nodes[closest_index]
                                closest_position = Position(closest[0], closest[1])
                                direction = pos.direction_to(closest_position)
                                mapping = {
                                    Constants.DIRECTIONS.CENTER: 0,
                                    Constants.DIRECTIONS.NORTH: 1,
                                    Constants.DIRECTIONS.WEST: 2,
                                    Constants.DIRECTIONS.SOUTH: 3,
                                    Constants.DIRECTIONS.EAST: 4,
                                }
                                obs[observation_index + mapping[direction]] = 1.0  # One-hot encoding direction

                                # 0 to 1 distance
                                distance = pos.distance_to(closest_position)
                                obs[observation_index + 5] = min(distance / 20.0, 1.0)

                                # 0 to 1 value (amount of resource, cargo for unit, or fuel for city)
                                if key == "city":
                                    # City fuel as % of upkeep for 200 turns
                                    c = game.cities[game.map.get_cell_by_pos(closest_position).city_tile.city_id]
                                    obs[observation_index + 6] = min(
                                        c.fuel / (c.get_light_upkeep() * 200.0),
                                        1.0
                                    )
                                elif key in [Constants.RESOURCE_TYPES.WOOD, Constants.RESOURCE_TYPES.COAL,
                                             Constants.RESOURCE_TYPES.URANIUM]:
                                    # Resource amount
                                    obs[observation_index + 6] = min(
                                        game.map.get_cell_by_pos(closest_position).resource.amount / 500,
                                        1.0
                                    )
                                else:
                                    # Unit cargo
                                    obs[observation_index + 6] = min(
                                        next(iter(game.map.get_cell_by_pos(
                                            closest_position).units.values())).get_cargo_space_left() / 100,
                                        1.0
                                    )

                    observation_index += 7

        if unit is not None:
            # Encode the cargo space
            #   1x cargo size
            obs[observation_index] = unit.get_cargo_space_left() / GAME_CONSTANTS["PARAMETERS"]["RESOURCE_CAPACITY"][
                "WORKER"]
            observation_index += 1
        else:
            observation_index += 1

        # Game state observations

        #   1x is night
        obs[observation_index] = game.is_night()
        observation_index += 1

        #   1x percent of game done
        obs[observation_index] = game.state["turn"] / GAME_CONSTANTS["PARAMETERS"]["MAX_DAYS"]
        observation_index += 1

        #   2x citytile counts [cur player, opponent]
        #   2x worker counts [cur player, opponent]
        #   2x cart counts [cur player, opponent]
        max_count = 30
        for key in ["city", str(Constants.UNIT_TYPES.WORKER), str(Constants.UNIT_TYPES.CART)]:
            if key in self.object_nodes:
                obs[observation_index] = len(self.object_nodes[key]) / max_count
            if (key + "_opponent") in self.object_nodes:
                obs[observation_index + 1] = len(self.object_nodes[(key + "_opponent")]) / max_count
            observation_index += 2

        #   1x research points [cur player]
        #   1x researched coal [cur player]
        #   1x researched uranium [cur player]
        obs[observation_index] = game.state["teamStates"][team]["researchPoints"] / 200.0
        obs[observation_index+1] = float(game.state["teamStates"][team]["researched"]["coal"])
        obs[observation_index+2] = float(game.state["teamStates"][team]["researched"]["uranium"])

        return obs

    def action_code_to_action(self, action_code, game, unit=None, city_tile=None, team=None):
        """
        Takes an action in the environment according to actionCode:
            actionCode: Index of action to take into the action array.
        Returns: An action.
        """
        # Map actionCode index into to a constructed Action object
        try:
            x = None
            y = None
            if city_tile is not None:
                x = city_tile.pos.x
                y = city_tile.pos.y
            elif unit is not None:
                x = unit.pos.x
                y = unit.pos.y
            
            if city_tile != None:
                action =  self.actionSpaceMapCities[action_code%len(self.actionSpaceMapCities)](
                    game=game,
                    unit_id=unit.id if unit else None,
                    unit=unit,
                    city_id=city_tile.city_id if city_tile else None,
                    citytile=city_tile,
                    team=team,
                    x=x,
                    y=y
                )

                # If the city action is invalid, default to research action automatically
                if not action.is_valid(game, actions_validated=[]):
                    action = ResearchAction(
                        game=game,
                        unit_id=unit.id if unit else None,
                        unit=unit,
                        city_id=city_tile.city_id if city_tile else None,
                        citytile=city_tile,
                        team=team,
                        x=x,
                        y=y
                    )
            else:
                action =  self.actionSpaceMapUnits[action_code%len(self.actionSpaceMapUnits)](
                    game=game,
                    unit_id=unit.id if unit else None,
                    unit=unit,
                    city_id=city_tile.city_id if city_tile else None,
                    citytile=city_tile,
                    team=team,
                    x=x,
                    y=y
                )
            
            return action
        except Exception as e:
            # Not a valid action
            print(e)
            return None

    def take_action(self, action_code, game, unit=None, city_tile=None, team=None):
        """
        Takes an action in the environment according to actionCode:
            actionCode: Index of action to take into the action array.
        """
        action = self.action_code_to_action(action_code, game, unit, city_tile, team)
        self.match_controller.take_action(action)
    
    def game_start(self, game):
        """
        This funciton is called at the start of each game. Use this to
        reset and initialize per game. Note that self.team may have
        been changed since last game. The game map has been created
        and starting units placed.

        Args:
            game ([type]): Game.
        """
        self.last_generated_fuel = game.stats["teamStats"][self.team]["fuelGenerated"]
        self.last_resources_collected = copy.deepcopy(game.stats["teamStats"][self.team]["resourcesCollected"])
        if self.stats != None:
            self.stats_last_game =  self.stats
        self.stats = {
            "rew/r_total": 0,
            "rew/r_wood": 0,
            "rew/r_coal": 0,
            "rew/r_uranium": 0,
            "rew/r_research": 0,
            "rew/r_city_tiles_end": 0,
            "rew/r_fuel_collected":0,
            "rew/r_units":0,
            "rew/r_city_tiles":0,
            "rew/r_units_opponent":0,
            "rew/r_city_tiles_opponent":0,
            "rew/r_opponent_city_tiles_end":0,
            "game/turns": 0,
            "game/research": 0,
            "game/unit_count": 0,
            "game/cart_count": 0,
            "game/city_count": 0,
            "game/city_tiles": 0,
            "game/wood_rate_mined": 0,
            "game/coal_rate_mined": 0,
            "game/uranium_rate_mined": 0,
            "game/opponent_city_tiles": 0,
            "game/opponent_unit_count": 0,
            "game/opponent_city_count": 0,
        }
        self.is_last_turn = False

        # Calculate starting map resources
        type_map = {
            Constants.RESOURCE_TYPES.WOOD: "WOOD",
            Constants.RESOURCE_TYPES.COAL: "COAL",
            Constants.RESOURCE_TYPES.URANIUM: "URANIUM",
        }

        self.fuel_collected_last = 0
        self.fuel_start = {}
        self.fuel_last = {}
        for type, type_upper in type_map.items():
            self.fuel_start[type] = 0
            self.fuel_last[type] = 0
            for c in game.map.resources_by_type[type]:
                self.fuel_start[type] += c.resource.amount * game.configs["parameters"]["RESOURCE_TO_FUEL_RATE"][type_upper]

        self.research_last = 0
        self.units_last = 0
        self.city_tiles_last = 0
        
        self.units_last_opponent = 0
        self.city_tiles_last_opponent = 0

    def turn_reward_weight(self):
        if self.step_count <= 90:
            return 1.0
        elif self.step_count <= 180:
            return 1.2
        elif self.step_count <= 270:
            return 1.5
        else:
            return 1.2
        
    def get_reward(self, game, is_game_finished, is_new_turn, is_game_error):
        """
        Returns the reward function for this step of the game.
        """
        if is_game_error:
            # Game environment step failed, assign a game lost reward to not incentivise this
            print("Game failed due to error")
            return -1.0

        if not is_new_turn and not is_game_finished:
            # Only apply rewards at the start of each turn
            return 0

        # Get some basic stats
        unit_count = len(game.state["teamStates"][self.team % 2]["units"])
        cart_count = 0
        for id, u in game.state["teamStates"][self.team % 2]["units"].items():
            if u.type == Constants.UNIT_TYPES.CART:
                cart_count += 1

        unit_count_opponent = len(game.state["teamStates"][(self.team + 1) % 2]["units"])
        research = min(game.state["teamStates"][self.team]["researchPoints"], 200.0) # Cap research points at 200
        city_count = 0
        city_count_opponent = 0
        city_tile_count = 0
        city_tile_count_opponent = 0
        for city in game.cities.values():
            if city.team == self.team:
                city_count += 1
            else:
                city_count_opponent += 1

            for cell in city.city_cells:
                if city.team == self.team:
                    city_tile_count += 1
                else:
                    city_tile_count_opponent += 1
        
        # Basic stats
        self.stats["game/research"] = research
        self.stats["game/city_tiles"] = city_tile_count
        self.stats["game/city_count"] = city_count
        self.stats["game/unit_count"] = unit_count
        self.stats["game/cart_count"] = cart_count
        self.stats["game/opponent_city_tiles"] = city_tile_count_opponent
        self.stats["game/opponent_unit_count"] = unit_count_opponent
        self.stats["game/opponent_city_count"] = city_count_opponent
        self.stats["game/turns"] = game.state["turn"]
        rewards = {}

        # Give up to 1.0 reward for each resource based on % of total mined.
        type_map = {
            Constants.RESOURCE_TYPES.WOOD: "WOOD",
            Constants.RESOURCE_TYPES.COAL: "COAL",
            Constants.RESOURCE_TYPES.URANIUM: "URANIUM",
        }
        fuel_now = {}
        for type, type_upper in type_map.items():
            fuel_now = game.stats["teamStats"][self.team]["resourcesCollected"][type] * game.configs["parameters"]["RESOURCE_TO_FUEL_RATE"][type_upper]
            rewards["rew/r_%s" % type] = (fuel_now - self.fuel_last[type]) / self.fuel_start[type] * self.turn_reward_weight()
            self.stats["game/%s_rate_mined" % type] = fuel_now / self.fuel_start[type]
            self.fuel_last[type] = fuel_now
        
        # Give more incentive for coal and uranium
        rewards["rew/r_%s" % Constants.RESOURCE_TYPES.COAL] *= 2
        rewards["rew/r_%s" % Constants.RESOURCE_TYPES.URANIUM] *= 4
        
        # Give a reward based on amount of fuel collected. 1.0 reward for each 20K fuel gathered.
        fuel_collected = game.stats["teamStats"][self.team]["fuelGenerated"]
        rewards["rew/r_fuel_collected"] = ( (fuel_collected - self.fuel_collected_last) / 20000 )
        self.fuel_collected_last = fuel_collected

        # Give a reward for unit creation/death. 0.05 reward per unit.
        rewards["rew/r_units"] = (unit_count - self.units_last) * 0.05
        rewards["rew/r_units_opponent"] = (unit_count_opponent - self.units_last_opponent) * -0.01
        self.units_last = unit_count
        self.units_last_opponent = unit_count_opponent

        # Give a reward for unit creation/death. 0.1 reward per city.
        rewards["rew/r_city_tiles"] = (city_tile_count - self.city_tiles_last) * 0.1
        rewards["rew/r_city_tiles_opponent"] = (city_tile_count_opponent - self.city_tiles_last_opponent) * -0.01
        self.city_tiles_last = city_tile_count
        self.city_tiles_last_opponent = city_tile_count_opponent

        # Tiny reward for research to help. Up to 0.5 reward for this.
        rewards["rew/r_research"] = (research - self.research_last) / (200 * 2)
        self.research_last = research
        
        # Give a reward up to around 50.0 based on number of city tiles at the end of the game
        rewards["rew/r_city_tiles_end"] = 0
        rewards["rew/r_opponent_city_tiles_end"] = 0
        if is_game_finished:
            self.is_last_turn = True
            rewards["rew/r_city_tiles_end"] = city_tile_count
            rewards["rew/r_opponent_city_tiles_end"] = -0.2 * city_tile_count_opponent
        
        
        # Update the stats and total reward
        reward = 0
        for name, value in rewards.items():
            self.stats[name] += value
            reward += value
        self.stats["rew/r_total"] += reward

        # Print the final game stats sometimes
        if is_game_finished and random.random() <= 0.15:
            stats_string = []
            for key, value in self.stats.items():
                stats_string.append("%s=%.2f" % (key, value))
            print(",".join(stats_string))

        self.step_count += 1
        return max(reward, 0)
        
    

    def process_turn(self, game, team):
        """
        Decides on a set of actions for the current turn. Not used in training, only inference.
        Returns: Array of actions to perform.
        """
        start_time = time.time()
        actions = []
        new_turn = True

        # Inference the model per-unit
        units = game.state["teamStates"][team]["units"].values()
        for unit in units:
            if unit.can_act():
                obs = self.get_observation(game, unit, None, unit.team, new_turn)
                action_code, _states = self.model.predict(obs, deterministic=False)
                if action_code is not None:
                    actions.append(
                        self.action_code_to_action(action_code, game=game, unit=unit, city_tile=None, team=unit.team))
                new_turn = False

        # Inference the model per-city
        cities = game.cities.values()
        for city in cities:
            if city.team == team:
                for cell in city.city_cells:
                    city_tile = cell.city_tile
                    if city_tile.can_act():
                        obs = self.get_observation(game, None, city_tile, city.team, new_turn)
                        action_code, _states = self.model.predict(obs, deterministic=False)
                        if action_code is not None:
                            actions.append(
                                self.action_code_to_action(action_code, game=game, unit=None, city_tile=city_tile,
                                                           team=city.team))
                        new_turn = False

        time_taken = time.time() - start_time
        if time_taken > 0.5:  # Warn if larger than 0.5 seconds.
            print("WARNING: Inference took %.3f seconds for computing actions. Limit is 1 second." % time_taken,
                  file=sys.stderr)

        return actions



Overwriting agent_policy.py


# Build the environment for training

Notes on metrics:
* An Episode is a single game between your RL agent and it's opponent. This is generally 360 turns, spanning more than 360 unit + city decision steps.
* Mean episode length (ep_len_mean) is the number of decision made per game. The larger this gets, means that it is making more unit + city decision per game, meaning that more units and cities were alive for longer during the game.
* Episode reward mean (ep_rew_mean), is set up as micro-reward funciton for faster learning. Per turn it gets a small reward based on the number of cities and units alive. It gets a really big reward based on the number of cities and units alive at the end of the game.

In [20]:
import argparse
import glob
import os
import random
from typing import Callable

from stable_baselines3 import PPO  # pip install stable-baselines3
from stable_baselines3.common.callbacks import CheckpointCallback
from stable_baselines3.common.utils import set_random_seed
from stable_baselines3.common.vec_env import SubprocVecEnv

from importlib import reload
import agent_policy
reload(agent_policy) # Reload the file from disk incase the above agent-writing cell block was edited
from agent_policy import AgentPolicy

from luxai2021.env.agent import Agent
from luxai2021.env.lux_env import LuxEnvironment
from luxai2021.game.constants import LuxMatchConfigs_Default


# Default Lux configs
configs = LuxMatchConfigs_Default

# Create a default opponent agent
opponent = AgentPolicy(mode="inference", model=PPO.load(f"models/rl_model_PPO_1_10000000_steps.zip"))

# Create a RL agent in training mode
player = AgentPolicy(mode="train")

# Create the Lux environment
env = LuxEnvironment(configs=configs,
                     learning_agent=player,
                     opponent_agent=opponent)

# Define the model, you can pick other RL algos from Stable Baselines3 instead if you like
#model = PPO("MlpPolicy",
#                env,
#                verbose=1,
#                tensorboard_log="./lux_tensorboard/",
#                learning_rate=0.001,
#                gamma=0.999,
#                gae_lambda=0.95,
#                batch_size=2048 * 8,
#                n_steps=2048 * 8
#            )
model = PPO.load(f"models/rl_model_PPO_1_10000000_steps.zip", env)
# Define a learning rate schedule
# (number of steps, learning_rate)
schedule = [
    (3000000, 0.01),
    (8000000, 0.001),
    (8000000, 0.0001),
]

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


Running in inference-only mode.


# Train the agent against a dummy opponent

In [21]:
from stable_baselines3.common.utils import get_schedule_fn

print("Training model...")
run_id = 1

# Save a checkpoint every 1M steps
checkpoint_callback = CheckpointCallback(save_freq=500000,
                                         save_path='./models/',
                                         name_prefix=f'rl_model_vs_PPO{run_id}')

# Train the policy
for steps, learning_rate in schedule:
    model.lr_schedule = get_schedule_fn(learning_rate)
    model.learn(total_timesteps=steps,
                callback=checkpoint_callback,
                reset_num_timesteps = False)

# Save final model
model.save(path=f'models/model.zip')

print("Done training model.")

Training model...
Logging to ./lux_tensorboard/PPO_0
rew/r_total=0.31,rew/r_wood=0.98,rew/r_coal=0.20,rew/r_uranium=0.00,rew/r_research=0.28,rew/r_city_tiles_end=0.00,rew/r_fuel_collected=0.14,rew/r_units=0.00,rew/r_city_tiles=0.00,rew/r_units_opponent=-0.03,rew/r_city_tiles_opponent=-0.06,rew/r_opponent_city_tiles_end=-1.20,game/turns=196.00,game/research=110.00,game/unit_count=0.00,game/cart_count=0.00,game/city_count=0.00,game/city_tiles=0.00,game/wood_rate_mined=0.98,game/coal_rate_mined=0.10,game/uranium_rate_mined=0.00,game/opponent_city_tiles=6.00,game/opponent_unit_count=3.00,game/opponent_city_count=1.00
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 2.12e+03 |
|    ep_rew_mean     | 8.41     |
| time/              |          |
|    fps             | 489      |
|    iterations      | 1        |
|    time_elapsed    | 33       |
|    total_timesteps | 10016384 |
---------------------------------
rew/r_total=6.53,rew/r_wood=1.17,rew/r_

rew/r_total=1.78,rew/r_wood=0.41,rew/r_coal=0.00,rew/r_uranium=0.00,rew/r_research=0.16,rew/r_city_tiles_end=1.00,rew/r_fuel_collected=0.06,rew/r_units=0.05,rew/r_city_tiles=0.10,rew/r_units_opponent=-0.00,rew/r_city_tiles_opponent=-0.00,rew/r_opponent_city_tiles_end=0.00,game/turns=159.00,game/research=65.00,game/unit_count=1.00,game/cart_count=0.00,game/city_count=1.00,game/city_tiles=1.00,game/wood_rate_mined=0.41,game/coal_rate_mined=0.00,game/uranium_rate_mined=0.00,game/opponent_city_tiles=0.00,game/opponent_unit_count=0.00,game/opponent_city_count=0.00
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.56e+03    |
|    ep_rew_mean          | 7.77        |
| time/                   |             |
|    fps                  | 568         |
|    iterations           | 8           |
|    time_elapsed         | 230         |
|    total_timesteps      | 10131072    |
| train/                  |             |
|    approx_kl

------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.58e+03     |
|    ep_rew_mean          | 7.49         |
| time/                   |              |
|    fps                  | 588          |
|    iterations           | 13           |
|    time_elapsed         | 361          |
|    total_timesteps      | 10212992     |
| train/                  |              |
|    approx_kl            | 0.0148552535 |
|    clip_fraction        | 0.0989       |
|    clip_range           | 0.2          |
|    entropy_loss         | -0.301       |
|    explained_variance   | 0.587        |
|    learning_rate        | 0.01         |
|    loss                 | 0.14         |
|    n_updates            | 6220         |
|    policy_gradient_loss | -0.000365    |
|    value_loss           | 0.296        |
------------------------------------------
rew/r_total=2.91,rew/r_wood=0.50,rew/r_coal=0.01,rew/r_uranium=0.00,rew/r_research=0.14,rew/r_cit

rew/r_total=26.46,rew/r_wood=2.14,rew/r_coal=0.93,rew/r_uranium=0.37,rew/r_research=0.50,rew/r_city_tiles_end=20.00,rew/r_fuel_collected=0.41,rew/r_units=0.55,rew/r_city_tiles=2.00,rew/r_units_opponent=-0.02,rew/r_city_tiles_opponent=-0.02,rew/r_opponent_city_tiles_end=-0.40,game/turns=360.00,game/research=200.00,game/unit_count=11.00,game/cart_count=0.00,game/city_count=2.00,game/city_tiles=20.00,game/wood_rate_mined=2.14,game/coal_rate_mined=0.46,game/uranium_rate_mined=0.09,game/opponent_city_tiles=2.00,game/opponent_unit_count=2.00,game/opponent_city_count=1.00
rew/r_total=9.12,rew/r_wood=0.84,rew/r_coal=0.01,rew/r_uranium=0.00,rew/r_research=0.46,rew/r_city_tiles_end=9.00,rew/r_fuel_collected=0.31,rew/r_units=0.20,rew/r_city_tiles=0.90,rew/r_units_opponent=-0.08,rew/r_city_tiles_opponent=-0.12,rew/r_opponent_city_tiles_end=-2.40,game/turns=360.00,game/research=182.00,game/unit_count=4.00,game/cart_count=0.00,game/city_count=2.00,game/city_tiles=9.00,game/wood_rate_mined=0.84,game/

rew/r_total=1.56,rew/r_wood=0.80,rew/r_coal=0.16,rew/r_uranium=0.00,rew/r_research=0.36,rew/r_city_tiles_end=0.00,rew/r_fuel_collected=0.10,rew/r_units=0.15,rew/r_city_tiles=0.00,rew/r_units_opponent=-0.00,rew/r_city_tiles_opponent=0.00,rew/r_opponent_city_tiles_end=0.00,game/turns=199.00,game/research=144.00,game/unit_count=3.00,game/cart_count=1.00,game/city_count=0.00,game/city_tiles=0.00,game/wood_rate_mined=0.80,game/coal_rate_mined=0.08,game/uranium_rate_mined=0.00,game/opponent_city_tiles=0.00,game/opponent_unit_count=0.00,game/opponent_city_count=0.00
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.54e+03     |
|    ep_rew_mean          | 9.4          |
| time/                   |              |
|    fps                  | 597          |
|    iterations           | 23           |
|    time_elapsed         | 630          |
|    total_timesteps      | 10376832     |
| train/                  |              |
|   

...

rew/r_total=10.23,rew/r_wood=1.53,rew/r_coal=0.28,rew/r_uranium=0.00,rew/r_research=0.35,rew/r_city_tiles_end=7.00,rew/r_fuel_collected=0.17,rew/r_units=0.20,rew/r_city_tiles=0.70,rew/r_units_opponent=0.00,rew/r_city_tiles_opponent=0.00,rew/r_opponent_city_tiles_end=0.00,game/turns=277.00,game/research=138.00,game/unit_count=4.00,game/cart_count=0.00,game/city_count=1.00,game/city_tiles=7.00,game/wood_rate_mined=1.53,game/coal_rate_mined=0.14,game/uranium_rate_mined=0.00,game/opponent_city_tiles=0.00,game/opponent_unit_count=0.00,game/opponent_city_count=0.00
-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 1.89e+03      |
|    ep_rew_mean          | 12.3          |
| time/                   |               |
|    fps                  | 618           |
|    iterations           | 466           |
|    time_elapsed         | 12346         |
|    total_timesteps      | 28661376      |
| train/                  |           

-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 1.92e+03      |
|    ep_rew_mean          | 12.4          |
| time/                   |               |
|    fps                  | 619           |
|    iterations           | 471           |
|    time_elapsed         | 12462         |
|    total_timesteps      | 28743296      |
| train/                  |               |
|    approx_kl            | 0.00048016594 |
|    clip_fraction        | 0.000726      |
|    clip_range           | 0.2           |
|    entropy_loss         | -0.241        |
|    explained_variance   | 0.375         |
|    learning_rate        | 0.0001        |
|    loss                 | 0.55          |
|    n_updates            | 17530         |
|    policy_gradient_loss | -0.000324     |
|    value_loss           | 1.12          |
-------------------------------------------
------------------------------------------
| rollout/                |      

------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.88e+03     |
|    ep_rew_mean          | 11.6         |
| time/                   |              |
|    fps                  | 619          |
|    iterations           | 477          |
|    time_elapsed         | 12605        |
|    total_timesteps      | 28841600     |
| train/                  |              |
|    approx_kl            | 0.0001526456 |
|    clip_fraction        | 3.05e-05     |
|    clip_range           | 0.2          |
|    entropy_loss         | -0.218       |
|    explained_variance   | 0.944        |
|    learning_rate        | 0.0001       |
|    loss                 | 0.0277       |
|    n_updates            | 17590        |
|    policy_gradient_loss | -0.000392    |
|    value_loss           | 0.0586       |
------------------------------------------
rew/r_total=2.63,rew/r_wood=0.83,rew/r_coal=0.17,rew/r_uranium=0.00,rew/r_research=0.37,rew/r_cit

rew/r_total=7.17,rew/r_wood=0.95,rew/r_coal=0.36,rew/r_uranium=0.00,rew/r_research=0.23,rew/r_city_tiles_end=5.00,rew/r_fuel_collected=0.08,rew/r_units=0.05,rew/r_city_tiles=0.50,rew/r_units_opponent=-0.00,rew/r_city_tiles_opponent=-0.00,rew/r_opponent_city_tiles_end=0.00,game/turns=235.00,game/research=90.00,game/unit_count=1.00,game/cart_count=0.00,game/city_count=2.00,game/city_tiles=5.00,game/wood_rate_mined=0.95,game/coal_rate_mined=0.18,game/uranium_rate_mined=0.00,game/opponent_city_tiles=0.00,game/opponent_unit_count=0.00,game/opponent_city_count=0.00
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.85e+03     |
|    ep_rew_mean          | 10.3         |
| time/                   |              |
|    fps                  | 620          |
|    iterations           | 482          |
|    time_elapsed         | 12718        |
|    total_timesteps      | 28923520     |
| train/                  |              |
|   

rew/r_total=2.05,rew/r_wood=0.73,rew/r_coal=0.10,rew/r_uranium=0.00,rew/r_research=0.44,rew/r_city_tiles_end=1.00,rew/r_fuel_collected=0.19,rew/r_units=0.15,rew/r_city_tiles=0.10,rew/r_units_opponent=-0.03,rew/r_city_tiles_opponent=-0.03,rew/r_opponent_city_tiles_end=-0.60,game/turns=360.00,game/research=175.00,game/unit_count=3.00,game/cart_count=0.00,game/city_count=1.00,game/city_tiles=1.00,game/wood_rate_mined=0.73,game/coal_rate_mined=0.05,game/uranium_rate_mined=0.00,game/opponent_city_tiles=3.00,game/opponent_unit_count=3.00,game/opponent_city_count=3.00
-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 1.9e+03       |
|    ep_rew_mean          | 12.4          |
| time/                   |               |
|    fps                  | 622           |
|    iterations           | 488           |
|    time_elapsed         | 12851         |
|    total_timesteps      | 29021824      |
| train/                  |         

In [21]:
# Save final model
model.save(path=f'models/model.zip')

print("Done training model.")

Done training model.


# Set up a Kaggle Submission and lux replay environment for the agent

In [22]:
"""
This downloads two required python package dependencies that are not pre-installed
by Kaggle yet.

This places the following two packages in the current working directory:
    luxai2021
    stable_baselines3
"""

import os
import shutil
import subprocess
import tempfile

def localize_package(git, branch, folder):
    if os.path.exists(folder):
        print("Already localized %s" % folder)
    else:
        # https://stackoverflow.com/questions/51239168/how-to-download-single-file-from-a-git-repository-using-python
        # Create temporary dir
        t = tempfile.mkdtemp()

        args = ['git', 'clone', '--depth=1', git, t, '-b', branch]
        res = subprocess.Popen(args, stdout=subprocess.PIPE)
        output, _error = res.communicate()

        if not _error:
            print(output)
        else:
            print(_error)
        
        # Copy desired file from temporary dir
        shutil.move(os.path.join(t, folder), '.')
        # Remove temporary dir
        shutil.rmtree(t, ignore_errors=True)

localize_package('https://github.com/glmcdona/LuxPythonEnvGym.git', 'main', 'luxai2021')
localize_package('https://github.com/glmcdona/LuxPythonEnvGym.git', 'main', 'kaggle_submissions')
localize_package('https://github.com/DLR-RM/stable-baselines3.git', 'master', 'stable_baselines3')

Already localized luxai2021
Already localized kaggle_submissions
Already localized stable_baselines3


In [23]:
# Move the dependent packages into kaggle submissions
!mv luxai2021 kaggle_submissions
!mv stable_baselines3 kaggle_submissions
!rm ./kaggle_submissions/agent_policy.py
!cp agent_policy.py kaggle_submissions

# Copy the agent and model to the submission 
!cp ./agent_policy.py kaggle_submissions
!cp ./models/model.zip kaggle_submissions

!ls kaggle_submissions

mv: rename luxai2021 to kaggle_submissions/luxai2021: Directory not empty
mv: rename stable_baselines3 to kaggle_submissions/stable_baselines3: Directory not empty
__pycache__              luxai2021                model.zip
agent_policy.py          main.py                  stable_baselines3
download_dependencies.py main_lux-ai-2021.py


In [24]:
from kaggle_environments import make
import json
# run another match but with our empty agent
env = make("lux_ai_2021", configuration={"seed": 5621242, "loglevel": 2, "annotations": True}, debug=True)

# Play the environment where the RL agent plays against itself
steps = env.run(["./kaggle_submissions/main.py", "./kaggle_submissions/main.py"])

Running in inference-only mode.
Running in inference-only mode.
[WARN] (match_5m1wdVo6Bci0) - turn 6; Unit u_3 collided when trying to move n to (14, 4)
[WARN] (match_5m1wdVo6Bci0) - turn 13; Unit u_5 collided when trying to move n to (15, 4)
[WARN] (match_5m1wdVo6Bci0) - turn 14; Unit u_5 collided when trying to move n to (15, 4)
[WARN] (match_5m1wdVo6Bci0) - turn 15; Unit u_6 collided when trying to move w to (1, 4)
[WARN] (match_5m1wdVo6Bci0) - turn 15; Unit u_5 collided when trying to move n to (15, 4)
[WARN] (match_5m1wdVo6Bci0) - turn 16; Unit u_5 collided when trying to move n to (15, 4)
[WARN] (match_5m1wdVo6Bci0) - turn 17; Unit u_5 collided when trying to move n to (15, 4)
[WARN] (match_5m1wdVo6Bci0) - turn 18; Unit u_3 collided when trying to move e to (15, 4)
[WARN] (match_5m1wdVo6Bci0) - turn 19; Unit u_5 collided when trying to move n to (15, 4)
[WARN] (match_5m1wdVo6Bci0) - Agent 0 tried to build unit on tile (0, 2) but unit cap reached. Build more CityTiles!; turn 20; c

[WARN] (match_5m1wdVo6Bci0) - turn 86; Unit u_11 collided when trying to move e to (11, 3)
[WARN] (match_5m1wdVo6Bci0) - turn 86; Unit u_2 collided when trying to move w to (11, 3)
[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to build unit on tile (10, 1) but unit cap reached. Build more CityTiles!; turn 87; cmd: bw 10 1
[WARN] (match_5m1wdVo6Bci0) - turn 87; Unit u_11 collided when trying to move e to (11, 3)
[WARN] (match_5m1wdVo6Bci0) - turn 87; Unit u_2 collided when trying to move w to (11, 3)
[WARN] (match_5m1wdVo6Bci0) - Agent 0 tried to build unit on tile (4, 4) but unit cap reached. Build more CityTiles!; turn 88; cmd: bw 4 4
[WARN] (match_5m1wdVo6Bci0) - turn 88; Unit u_11 collided when trying to move e to (11, 3)
[WARN] (match_5m1wdVo6Bci0) - turn 88; Unit u_2 collided when trying to move w to (11, 3)
[WARN] (match_5m1wdVo6Bci0) - turn 88; Unit u_27 collided when trying to move w to (10, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 89; Unit u_11 collided when trying to move e to (11

[WARN] (match_5m1wdVo6Bci0) - turn 122; Unit u_12 collided when trying to move n to (6, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 122; Unit u_19 collided when trying to move w to (9, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 123; Unit u_12 collided when trying to move n to (6, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 124; Unit u_20 collided when trying to move w to (9, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 125; Unit u_12 collided when trying to move w to (5, 2)
[WARN] (match_5m1wdVo6Bci0) - Agent 0 tried to move unit u_8 onto opponent CityTile; turn 126; cmd: m u_8 n
[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to build unit on tile (5, 1) but unit cap reached. Build more CityTiles!; turn 126; cmd: bw 5 1
[WARN] (match_5m1wdVo6Bci0) - turn 126; Unit u_12 collided when trying to move w to (5, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 126; Unit u_15 collided when trying to move n to (4, 1)
[WARN] (match_5m1wdVo6Bci0) - turn 126; Unit u_5 collided when trying to move w to (4, 1)
[WARN] (match_5m1wdVo6Bci

[WARN] (match_5m1wdVo6Bci0) - turn 143; Unit u_12 collided when trying to move w to (4, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 143; Unit u_19 collided when trying to move w to (7, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 143; Unit u_23 collided when trying to move w to (9, 2)
[WARN] (match_5m1wdVo6Bci0) - Agent 0 tried to move unit u_8 onto opponent CityTile; turn 144; cmd: m u_8 n
[WARN] (match_5m1wdVo6Bci0) - turn 144; Unit u_12 collided when trying to move w to (4, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 144; Unit u_19 collided when trying to move w to (7, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 144; Unit u_23 collided when trying to move w to (9, 2)
[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to move unit u_42 onto opponent CityTile; turn 145; cmd: m u_42 w
[WARN] (match_5m1wdVo6Bci0) - turn 145; Unit u_19 collided when trying to move w to (7, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 145; Unit u_23 collided when trying to move w to (9, 2)
[WARN] (match_5m1wdVo6Bci0) - turn 147; Unit u_17 coll

[WARN] (match_5m1wdVo6Bci0) - Agent 0 tried to move unit u_61 onto opponent CityTile; turn 214; cmd: m u_61 n
[WARN] (match_5m1wdVo6Bci0) - turn 214; Unit u_79 collided when trying to move e to (14, 13)
[WARN] (match_5m1wdVo6Bci0) - Agent 0 tried to move unit u_61 onto opponent CityTile; turn 215; cmd: m u_61 e
[WARN] (match_5m1wdVo6Bci0) - turn 215; Unit u_79 collided when trying to move e to (14, 13)
[WARN] (match_5m1wdVo6Bci0) - Agent 0 tried to move unit u_61 onto opponent CityTile; turn 216; cmd: m u_61 n
[WARN] (match_5m1wdVo6Bci0) - Agent 0 tried to move unit u_61 onto opponent CityTile; turn 217; cmd: m u_61 n
[WARN] (match_5m1wdVo6Bci0) - Agent 0 tried to move unit u_61 onto opponent CityTile; turn 218; cmd: m u_61 n
[WARN] (match_5m1wdVo6Bci0) - Agent 0 tried to build unit on tile (13, 13) but unit cap reached. Build more CityTiles!; turn 218; cmd: bw 13 13
[WARN] (match_5m1wdVo6Bci0) - turn 218; Unit u_79 collided when trying to move e to (14, 13)
[WARN] (match_5m1wdVo6Bci0)

[WARN] (match_5m1wdVo6Bci0) - turn 275; Unit u_96 collided when trying to move w to (3, 11)
[WARN] (match_5m1wdVo6Bci0) - turn 276; Unit u_96 collided when trying to move w to (3, 11)
[WARN] (match_5m1wdVo6Bci0) - turn 277; Unit u_97 collided when trying to move w to (3, 11)
[WARN] (match_5m1wdVo6Bci0) - turn 278; Unit u_96 collided when trying to move w to (3, 11)
[WARN] (match_5m1wdVo6Bci0) - turn 279; Unit u_96 collided when trying to move w to (3, 11)
[WARN] (match_5m1wdVo6Bci0) - turn 280; Unit u_96 collided when trying to move w to (3, 11)
[WARN] (match_5m1wdVo6Bci0) - turn 281; Unit u_96 collided when trying to move w to (3, 11)
[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to build unit on tile (4, 11) but unit cap reached. Build more CityTiles!; turn 282; cmd: bw 4 11
[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to build unit on tile (3, 11) but unit cap reached. Build more CityTiles!; turn 282; cmd: bw 3 11
[WARN] (match_5m1wdVo6Bci0) - turn 282; Unit u_111 collided when trying 

[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to move unit u_96 onto opponent CityTile; turn 309; cmd: m u_96 s
[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to move unit u_97 onto opponent CityTile; turn 309; cmd: m u_97 s
[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to move unit u_105 onto opponent CityTile; turn 309; cmd: m u_105 s
[WARN] (match_5m1wdVo6Bci0) - turn 309; Unit u_95 collided when trying to move s to (2, 12)
[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to move unit u_96 onto opponent CityTile; turn 310; cmd: m u_96 s
[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to move unit u_97 onto opponent CityTile; turn 310; cmd: m u_97 s
[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to move unit u_105 onto opponent CityTile; turn 310; cmd: m u_105 s
[WARN] (match_5m1wdVo6Bci0) - turn 310; Unit u_95 collided when trying to move s to (2, 12)
[WARN] (match_5m1wdVo6Bci0) - Agent 1 tried to move unit u_96 onto opponent CityTile; turn 311; cmd: m u_96 s
[WARN] (match_5m1wdVo6Bci0) - Agent 1 trie

In [25]:
# Render the match
env.render(mode="ipython", width=1200, height=800)

# Prepare and submit the kaggle submission

In [12]:
!tar -czf submission.tar.gz -C kaggle_submissions .
!ls

__pycache__
agent_policy.py
download_dependencies.py
kaggle_submissions
log.txt
lux_tensorboard
luxai2021
main.py
main_lux-ai-2021.py
models
reinforcement-learning-openai-ppo-with-python-game.ipynb
stable_baselines3
submission.tar.gz
